In [ ]:
!pip install Pillow
!pip install timm
!pip install flash_attn
!pip install torch
!pip install torchvision
!pip install datasets
!pip install transformers
!pip install sentencepiece

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 29.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 37.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for flash_attn: filename=flash_attn-2.6.3-cp310-cp310-linux_x86_64.whl size=187309225 sha256=237ef9c6157db394e1ddde4ba609a21ebb98382377a27041edc09318801a6f24
  Stored in directory: /root/.cache/pip/wheels/7e/e3/c3/89c7a2f3c4adc07cd1c675f8bb7b9ad4d18f64a72bccdfe826
Successfully built flash_attn
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.3/474.3 kB 16.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 19.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.6 MB/s eta 0:00:00
  Attempt

In [ ]:
import numpy as np
import torch
import torchvision.transforms as T
# from decord import VideoReader, cpu
from PIL import Image
from torchvision.transforms.functional import InterpolationMode
from transformers import AutoModel, AutoTokenizer

IMAGENET_MEAN = (0.485, 0.456, 0.406)
IMAGENET_STD = (0.229, 0.224, 0.225)

def build_transform(input_size):
    MEAN, STD = IMAGENET_MEAN, IMAGENET_STD
    transform = T.Compose([
        T.Lambda(lambda img: img.convert('RGB') if img.mode != 'RGB' else img),
        T.Resize((input_size, input_size), interpolation=InterpolationMode.BICUBIC),
        T.ToTensor(),
        T.Normalize(mean=MEAN, std=STD)
    ])
    return transform

def find_closest_aspect_ratio(aspect_ratio, target_ratios, width, height, image_size):
    best_ratio_diff = float('inf')
    best_ratio = (1, 1)
    area = width * height
    for ratio in target_ratios:
        target_aspect_ratio = ratio[0] / ratio[1]
        ratio_diff = abs(aspect_ratio - target_aspect_ratio)
        if ratio_diff < best_ratio_diff:
            best_ratio_diff = ratio_diff
            best_ratio = ratio
        elif ratio_diff == best_ratio_diff:
            if area > 0.5 * image_size * image_size * ratio[0] * ratio[1]:
                best_ratio = ratio
    return best_ratio

def dynamic_preprocess(image, min_num=1, max_num=12, image_size=448, use_thumbnail=False):
    orig_width, orig_height = image.size
    aspect_ratio = orig_width / orig_height

    # calculate the existing image aspect ratio
    target_ratios = set(
        (i, j) for n in range(min_num, max_num + 1) for i in range(1, n + 1) for j in range(1, n + 1) if
        i * j <= max_num and i * j >= min_num)
    target_ratios = sorted(target_ratios, key=lambda x: x[0] * x[1])

    # find the closest aspect ratio to the target
    target_aspect_ratio = find_closest_aspect_ratio(
        aspect_ratio, target_ratios, orig_width, orig_height, image_size)

    # calculate the target width and height
    target_width = image_size * target_aspect_ratio[0]
    target_height = image_size * target_aspect_ratio[1]
    blocks = target_aspect_ratio[0] * target_aspect_ratio[1]

    # resize the image
    resized_img = image.resize((target_width, target_height))
    processed_images = []
    for i in range(blocks):
        box = (
            (i % (target_width // image_size)) * image_size,
            (i // (target_width // image_size)) * image_size,
            ((i % (target_width // image_size)) + 1) * image_size,
            ((i // (target_width // image_size)) + 1) * image_size
        )
        # split the image
        split_img = resized_img.crop(box)
        processed_images.append(split_img)
    assert len(processed_images) == blocks
    if use_thumbnail and len(processed_images) != 1:
        thumbnail_img = image.resize((image_size, image_size))
        processed_images.append(thumbnail_img)
    return processed_images

def load_image(image_file, input_size=448, max_num=12):
    image = Image.open(image_file).convert('RGB')
    transform = build_transform(input_size=input_size)
    images = dynamic_preprocess(image, image_size=input_size, use_thumbnail=True, max_num=max_num)
    pixel_values = [transform(image) for image in images]
    pixel_values = torch.stack(pixel_values)
    return pixel_values

model = AutoModel.from_pretrained(
    "5CD-AI/Vintern-1B-v2",
    torch_dtype=torch.bfloat16,
    low_cpu_mem_usage=True,
    trust_remote_code=True,
).eval().cuda()
tokenizer = AutoTokenizer.from_pretrained("5CD-AI/Vintern-1B-v2", trust_remote_code=True, use_fast=False)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/5.33k [00:00<?, ?B/s]

configuration_internvl_chat.py:   0%|          | 0.00/3.80k [00:00<?, ?B/s]

configuration_intern_vit.py:   0%|          | 0.00/5.55k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/5CD-AI/Vintern-1B-v2:
- configuration_intern_vit.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/5CD-AI/Vintern-1B-v2:
- configuration_internvl_chat.py
- configuration_intern_vit.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


...

tokenizer_config.json:   0%|          | 0.00/3.02k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/3.38M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.67M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/265 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/498 [00:00<?, ?B/s]

In [ ]:
torch.backends.cuda.enable_mem_efficient_sdp(False)
torch.backends.cuda.enable_flash_sdp(False)

In [ ]:
import pandas as pd
df = pd.read_csv('/content/test.csv')[:1000]
# df = pd.read_csv('/content/sample_test.csv')

df.tail()

index                                         image_link  group_id  \
995    996  https://m.media-amazon.com/images/I/31g2J-R9WW...    244283   
996    997  https://m.media-amazon.com/images/I/31gAWNuH78...    639090   
997    998  https://m.media-amazon.com/images/I/31gDnvm3iW...    884560   
998    999  https://m.media-amazon.com/images/I/31gKQYdhgN...    226504   
999   1000  https://m.media-amazon.com/images/I/31gT4NLWg5...    271537   

     entity_name  
995        width  
996  item_weight  
997  item_weight  
998  item_weight  
999      voltage

In [ ]:
import os
from urllib.parse import urlparse

img_list = []
# URL of the image
for img_url in df['image_link']:
  # Parse the URL and extract the image name
  parsed_url = urlparse(img_url)
  image_name = os.path.basename(parsed_url.path)
  img_list.append(image_name)

In [ ]:
import requests
import os
os.mkdir('images')
i = 0
for link in df['image_link']:

  # Send a request to fetch the image
  response = requests.get(link)

  # Save the image locally
  with open(f"/content/images/{img_list[i]}", "wb") as file:
      file.write(response.content)
  i+=1

In [ ]:
import re

def process_images_in_batches(image_links, batch_size=25):
    ans = []
    total_images = len(image_links)

    for i in range(0, total_images, batch_size):
        batch = image_links[i:i+batch_size]
        for j, url in enumerate(batch):
            try:
                test_image = f"/content/images/{img_list[i+j]}"

                # Try to load and process the image
                pixel_values = load_image(test_image, max_num=12).to(torch.bfloat16).cuda()
                generation_config = dict(max_new_tokens=1024, do_sample=False, num_beams=3, repetition_penalty=2.5)

                question = f'<image>\nWhat is the {df.entity_name[i+j]}?'

                def save_model(model, save_path='/content/sample_data/model_complete.pth'):
                  torch.save(model.state_dict(), save_path)
                  print(f'Model saved to {save_path}')

                # Generate response from the model
                response, history = model.chat(tokenizer, pixel_values, question, generation_config, history=None, return_history=True)

                def extract_weight(reply):
                    pattern = r'(\d+)(\D*)'
                    matches = re.findall(pattern, reply, re.IGNORECASE)
                    result = ' '.join(f'{match[0]}{match[1]}' for match in matches)
                    return result

                # Try to clean and extract the weight
                cleaned_weight = extract_weight(response).strip()
                if cleaned_weight and cleaned_weight[-1] == '.':
                    cleaned_weight = cleaned_weight[:-1]

            except Exception as e:
                # Handle bad requests or any other errors
                print(f"Error processing image {i+j+1}: {e}")
                cleaned_weight = ''  # Append an empty string in case of an error

            ans.append(cleaned_weight)
            print(f'Response for image {i+j+1}.')

        # Save the model after processing each batch
        save_model(model)

    return ans

# Process images in batches
ans = process_images_in_batches(df['image_link'], batch_size=25)





Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Response for image 1.


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Response for image 2.


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


...

Response for image 998.


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Response for image 999.


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Response for image 1000.
Model saved to /content/sample_data/model_complete.pth


In [ ]:
# model = torch.load('/content/sample_data/model_complete.pth')


#**Production code**

In [44]:
import pandas as pd
df = pd.read_csv('/content/test.csv')
print(len(df))

index_col = df['index']
index_col.to_csv('/content/sample_test_out.csv', index=False)

131187


In [45]:
ans = pd.DataFrame(ans, columns=['prediction'])

In [46]:
data = pd.read_csv('/content/sample_test_out.csv')

data['prediction'] = ans['prediction']

# Save the updated DataFrame back to a CSV
data.to_csv('/content/sample_test_out.csv', index=False)

In [47]:
data_frame_to_be_added = df['entity_name']
data_frame_to_be_added = pd.DataFrame({'entity_name': data_frame_to_be_added})

# Concatenate DataFrames (row-wise)
combined_df = pd.concat([ans, data_frame_to_be_added.reset_index(drop=True)], axis=1)

(combined_df)

prediction                    entity_name
0                91. 4cm                         height
1          42cm/ 16. 54"                          width
2          42cm/ 16. 54"                         height
3          42cm/ 16. 54"                          depth
4       10. 50cm/ 4. 13"                          depth
...                  ...                            ...
131182               NaN  maximum_weight_recommendation
131183               NaN                    item_weight
131184               NaN  maximum_weight_recommendation
131185               NaN                    item_weight
131186               NaN  maximum_weight_recommendation

[131187 rows x 2 columns]

In [48]:
entity_unit_map = {
    'width': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'depth': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'height': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'item_weight': {'gram',
        'kilogram',
        'microgram',
        'milligram',
        'ounce',
        'pound',
        'ton'},
    'maximum_weight_recommendation': {'gram',
        'kilogram',
        'microgram',
        'milligram',
        'ounce',
        'pound',
        'ton'},
    'voltage': {'kilovolt', 'millivolt', 'volt'},
    'wattage': {'kilowatt', 'watt'},
    'item_volume': {'centilitre',
        'cubic foot',
        'cubic inch',
        'cup',
        'decilitre',
        'fluid ounce',
        'gallon',
        'imperial gallon',
        'litre',
        'microlitre',
        'millilitre',
        'pint',
        'quart'}
}

entity_unit_2d_list = [[category, list(units)] for category, units in entity_unit_map.items()]

# Print the resulting 2D list
for item in entity_unit_2d_list:
    print(item)

['width', ['metre', 'centimetre', 'inch', 'millimetre', 'foot', 'yard']]
['depth', ['metre', 'centimetre', 'inch', 'millimetre', 'foot', 'yard']]
['height', ['metre', 'centimetre', 'inch', 'millimetre', 'foot', 'yard']]
['item_weight', ['kilogram', 'ton', 'ounce', 'gram', 'pound', 'microgram', 'milligram']]
['maximum_weight_recommendation', ['kilogram', 'ton', 'ounce', 'gram', 'pound', 'microgram', 'milligram']]
['voltage', ['volt', 'kilovolt', 'millivolt']]
['wattage', ['watt', 'kilowatt']]
['item_volume', ['imperial gallon', 'microlitre', 'pint', 'millilitre', 'cup', 'fluid ounce', 'cubic foot', 'decilitre', 'centilitre', 'litre', 'quart', 'gallon', 'cubic inch']]


In [49]:
li = []
for i in combined_df['prediction']:
  li.append(str(i).lower().replace(' ', ''))
li

['91.4cm',
 '42cm/16.54"',
 '42cm/16.54"',
 '42cm/16.54"',
 '10.50cm/4.13"',
 '10.50cm/4.13"',
 '10.50cm/4.13"',
 '5.5inches',
 '40cm',
 '40cm',
 '1tb',
 '30.6cm',
 '10cm',
 '4.3inches',
 '4.3inches',
 '9lb(4kg)',
 '100kg',
 '208-240v16a60hz',
 '208-240v16a60hz',
 '208-240v',
 '76cm',
 '14inches',
 '15ml',
 '32cm',
 '32cm',
 '3.8inch',
 '3.8inches',
 '320gb',
 '1.140-1380g',
 '2.62lbs',
 '19cm/7yg',
 "200mm/8'",
 '5.8inches',
 '5.8inches',
 '5.8inches',
 '3lbs',
 '102.9-194.3cm',
 '4000kv',
 '4000k',
 '90cm',
 '90cm',
 '9inches',
 '96inches',
 '96inches',
 '41cm',
 '5.8in',
 '5.8in',
 '5.8in',
 '47inches',
 '90cm',
 '90cm',
 '200mm/8"',
 '200mm/8"',
 '7.58inches',
 '7.58in',
 '12.7cm',
 '8tb',
 '90cm',
 '90cm',
 '5w',
 '5v',
 '1.5kg',
 '280mm',
 '280mm',
 '280mm',
 '10440v',
 '1.92tb',
 '79-151"(200.7-383.5cm)',
 '4.2in',
 '4.2inches(10cm)',
 '4.2inches(10cm)',
 '9.1inches',
 '9.1inches(23cm)',
 '9.1inches(23cm)',
 '1500w',
 '1500w',
 '4.7in/12cm',
 '4.7in/12cm',
 '3kg',
 '120cm',
 '25

In [50]:
from collections import OrderedDict
import re

# Refined regex patterns with better flexibility
unit_patterns = {
    'centimetre': r'(?:cm|centimetre|centimeter|c\.m)',
    'foot': r'(?:ft|feet|foot)',
    'inch': r'(?:in|inch|")',
    'metre': r'(?:m|metre|meter)',
    'millimetre': r'(?:mm|millimetre|millimeter)',
    'yard': r'(?:yd|yard)',
    'gram': r'(?:g|gram)',
    'kilogram': r'(?:kg|kilogram)',
    'ounce': r'(?:oz|ounce)',
    'pound': r'(?:lbs?|pound)',
    'ton': r'(?:ton)',
    'volt': r'(?:v|volt)',
    'watt': r'(?:w|watt)',
    'litre': r'(?:l|litre|liter)',
    'fluid ounce': r'(?:fl oz|fluid ounce)'
}

def clean_data(raw_string):
    raw_string = re.sub(r'[^\w\s./\d]', '', raw_string)  # Remove unwanted characters
    raw_string = raw_string.lower().strip()  # Convert to lowercase and strip spaces
    return raw_string

def extract_value_unit(text):
    for unit, pattern in unit_patterns.items():
        match = re.search(r'(\d+(\.\d+)?\s*)' + pattern, text, re.IGNORECASE)  # Handles cases with no space
        if match:
            return match.group(1).strip(), unit  # Return the value and the standardized unit
    return None, None

def map_to_entity(unit):
    for entity, units in entity_unit_map.items():
        if unit in units:
            return entity
    return None

def process_output(raw_data_list):
    # Create an OrderedDict to preserve insertion order
    results = OrderedDict()

    # Initialize all categories with blank strings for every entry in the raw data
    for entity in entity_unit_map:
        results[entity] = [""] * len(raw_data_list)  # Placeholder for each item in the list

    # Fill in the results dictionary
    for i, raw_string in enumerate(raw_data_list):
        cleaned_string = clean_data(raw_string)

        # Split combined units like '90inches229cm'
        split_strings = re.findall(r'\d+\.?\d*\s*[a-zA-Z]+', cleaned_string)

        for split_string in split_strings:
            value, unit = extract_value_unit(split_string)
            if value and unit:
                entity = map_to_entity(unit)
                if entity:
                    results[entity][i] = f"{value} {unit}"  # Add value only to the matching entity

    # Resolve conflicts
    for i in range(len(raw_data_list)):
        seen_values = {}
        for entity, values in results.items():
            value = values[i]
            if value:
                if value in seen_values:
                    # Conflict detected
                    results[entity][i] = ""  # Clear the value to resolve conflict
                else:
                    seen_values[value] = entity
    return results

# Process the raw data list
mapped_output = process_output(li)

# Print the output in order
for entity, values in mapped_output.items():
    print(f"{entity}: {values}")

width: ['91.4 centimetre', '42 centimetre', '42 centimetre', '42 centimetre', '10.50 centimetre', '10.50 centimetre', '10.50 centimetre', '5.5 inch', '40 centimetre', '40 centimetre', '', '30.6 centimetre', '10 centimetre', '4.3 inch', '4.3 inch', '', '', '', '', '', '76 centimetre', '14 inch', '15 metre', '32 centimetre', '32 centimetre', '3.8 inch', '3.8 inch', '', '', '', '19 centimetre', '200 metre', '5.8 inch', '5.8 inch', '5.8 inch', '', '9194.3 centimetre', '', '', '90 centimetre', '90 centimetre', '9 inch', '96 inch', '96 inch', '41 centimetre', '5.8 inch', '5.8 inch', '5.8 inch', '47 inch', '90 centimetre', '90 centimetre', '200 metre', '200 metre', '7.58 inch', '7.58 inch', '12.7 centimetre', '', '90 centimetre', '90 centimetre', '', '', '', '280 metre', '280 metre', '280 metre', '', '', '7383.5 centimetre', '4.2 inch', '10 centimetre', '10 centimetre', '9.1 inch', '23 centimetre', '23 centimetre', '', '', '12 centimetre', '12 centimetre', '', '120 centimetre', '', '', '', ''

In [51]:
from collections import OrderedDict
import re

# Define the entity_unit_map
entity_unit_map = {
    'width': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'depth': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'height': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'item_weight': {'gram', 'kilogram', 'microgram', 'milligram', 'ounce', 'pound', 'ton'},
    'maximum_weight_recommendation': {'gram', 'kilogram', 'microgram', 'milligram', 'ounce', 'pound', 'ton'},
    'voltage': {'kilovolt', 'millivolt', 'volt'},
    'wattage': {'kilowatt', 'watt'},
    'item_volume': {'centilitre', 'cubic foot', 'cubic inch', 'cup', 'decilitre', 'fluid ounce', 'gallon',
                    'imperial gallon', 'litre', 'microlitre', 'millilitre', 'pint', 'quart'}
}

# Refined regex patterns with better flexibility
unit_patterns = {
    'centimetre': r'(?:cm|centimetre|centimeter|c\.m)',
    'foot': r'(?:ft|feet|foot)',
    'inch': r'(?:in|inch|")',
    'metre': r'(?:m|metre|meter)',
    'millimetre': r'(?:mm|millimetre|millimeter)',
    'yard': r'(?:yd|yard)',
    'gram': r'(?:g|gram)',
    'kilogram': r'(?:kg|kilogram)',
    'ounce': r'(?:oz|ounce)',
    'pound': r'(?:lbs?|pound)',
    'ton': r'(?:ton)',
    'volt': r'(?:v|volt)',
    'watt': r'(?:w|watt)',
    'litre': r'(?:l|litre|liter)',
    'fluid ounce': r'(?:fl oz|fluid ounce)'
}

def clean_data(raw_string):
    raw_string = re.sub(r'[^\w\s./\d]', '', raw_string)  # Remove unwanted characters
    raw_string = raw_string.lower().strip()  # Convert to lowercase and strip spaces
    return raw_string

def extract_value_unit(text):
    for unit, pattern in unit_patterns.items():
        match = re.search(r'(\d+(\.\d+)?\s*)' + pattern, text, re.IGNORECASE)  # Handles cases with no space
        if match:
            return match.group(1).strip(), unit  # Return the value and the standardized unit
    return None, None

def map_to_entity(unit):
    for entity, units in entity_unit_map.items():
        if unit in units:
            return entity
    return None

def process_output(raw_data_list):
    # Create an OrderedDict to preserve insertion order
    results = OrderedDict()

    # Initialize all categories with blank strings for every entry in the raw data
    for entity in entity_unit_map:
        results[entity] = [""] * len(raw_data_list)  # Placeholder for each item in the list

    for i, raw_string in enumerate(raw_data_list):
        cleaned_string = clean_data(raw_string)

        # Split combined units like '90inches229cm'
        split_strings = re.findall(r'\d+\.?\d*\s*[a-zA-Z]+', cleaned_string)

        for split_string in split_strings:
            value, unit = extract_value_unit(split_string)
            if value and unit:
                entity = map_to_entity(unit)
                if entity:
                    results[entity][i] = f"{value} {unit}"  # Add value only to the matching entity

    # Merge all results into a single list
    merged_list = [' '.join(filter(None, [results[entity][i] for entity in entity_unit_map])) for i in range(len(raw_data_list))]

    return merged_list

# Process the raw data list
mapped_output = process_output(li)
# mapped_output[80]
print(mapped_output)

['91.4 centimetre', '42 centimetre', '42 centimetre', '42 centimetre', '10.50 centimetre', '10.50 centimetre', '10.50 centimetre', '5.5 inch', '40 centimetre', '40 centimetre', '', '30.6 centimetre', '10 centimetre', '4.3 inch', '4.3 inch', '4 kilogram', '100 kilogram', '208240 volt', '208240 volt', '208240 volt', '76 centimetre', '14 inch', '15 metre', '32 centimetre', '32 centimetre', '3.8 inch', '3.8 inch', '320 gram', '1.1401380 gram', '2.62 pound', '19 centimetre', '200 metre', '5.8 inch', '5.8 inch', '5.8 inch', '3 pound', '9194.3 centimetre', '', '', '90 centimetre', '90 centimetre', '9 inch', '96 inch', '96 inch', '41 centimetre', '5.8 inch', '5.8 inch', '5.8 inch', '47 inch', '90 centimetre', '90 centimetre', '200 metre', '200 metre', '7.58 inch', '7.58 inch', '12.7 centimetre', '', '90 centimetre', '90 centimetre', '5 watt', '5 volt', '1.5 kilogram', '280 metre', '280 metre', '280 metre', '10440 volt', '', '7383.5 centimetre', '4.2 inch', '10 centimetre', '10 centimetre', '9.

In [58]:
for i, text in enumerate(mapped_output):
    words = text.split()

    # Check if word count is greater than 2, if so, keep only the first 2 words
    if len(words) > 2:
        words = words[:2]  # Keep only the first 2 words

    # Join the words back into a string
    mapped_output[i] = ' '.join(words)

# Check the modified mapped_output
mapped_output

['91.4 centimetre',
 '42 centimetre',
 '42 centimetre',
 '42 centimetre',
 '10.50 centimetre',
 '10.50 centimetre',
 '10.50 centimetre',
 '5.5 inch',
 '40 centimetre',
 '40 centimetre',
 '',
 '30.6 centimetre',
 '10 centimetre',
 '4.3 inch',
 '4.3 inch',
 '4 kilogram',
 '100 kilogram',
 '208240 volt',
 '208240 volt',
 '208240 volt',
 '76 centimetre',
 '14 inch',
 '15 metre',
 '32 centimetre',
 '32 centimetre',
 '3.8 inch',
 '3.8 inch',
 '320 gram',
 '1.1401380 gram',
 '2.62 pound',
 '19 centimetre',
 '200 metre',
 '5.8 inch',
 '5.8 inch',
 '5.8 inch',
 '3 pound',
 '9194.3 centimetre',
 '',
 '',
 '90 centimetre',
 '90 centimetre',
 '9 inch',
 '96 inch',
 '96 inch',
 '41 centimetre',
 '5.8 inch',
 '5.8 inch',
 '5.8 inch',
 '47 inch',
 '90 centimetre',
 '90 centimetre',
 '200 metre',
 '200 metre',
 '7.58 inch',
 '7.58 inch',
 '12.7 centimetre',
 '',
 '90 centimetre',
 '90 centimetre',
 '5 watt',
 '5 volt',
 '1.5 kilogram',
 '280 metre',
 '280 metre',
 '280 metre',
 '10440 volt',
 '',
 '73

In [59]:
df = pd.DataFrame(mapped_output, columns=['prediction'])
data['prediction'] = df['prediction']
data.to_csv('/content/sample_test_out.csv', index=False)


#**delete contents**

In [ ]:
import os

def list_directory_contents(directory_path):
    try:
        # Get a list of files and directories in the specified path
        contents = os.listdir(directory_path)

        print(f"Contents of '{directory_path}':")
        for item in contents:
            # Create the full path to the item
            item_path = os.path.join(directory_path, item)

            if os.path.isdir(item_path):
                print(f"[DIR]  {item}")
            else:
                print(f"[FILE] {item}")

    except FileNotFoundError:
        print(f"The directory '{directory_path}' does not exist.")
    except PermissionError:
        print(f"Permission denied to access '{directory_path}'.")

# Example usage
directory_path = '/content/images'
list_directory_contents(directory_path)

Contents of '/content/images':
[FILE] 31B43FuEJSL.jpg
[FILE] 314J9z-v4HL.jpg
[FILE] 31MSh7g6jHL.jpg
[FILE] 31tQMZp3k+L.jpg
[FILE] 31FCBht4h-L.jpg
[FILE] 31GO0eUnE7L.jpg
[FILE] 31TJEvx5qHL.jpg
[FILE] 31Q+s7UnpGL.jpg
[FILE] 21bwWoCpGJL.jpg
[FILE] 31OFG4xW+cL.jpg
[FILE] 41+9mJFvvxL.jpg
[FILE] 310PNQ4FmqL.jpg
[FILE] 317e7XKMYmS.jpg
[FILE] 31q4F28dP6L.jpg
[FILE] 31jSCvFq5-L.jpg
[FILE] 31RopGzufiL.jpg
[FILE] 31HkazRRetL.jpg
[FILE] 31JVaJ+Ks6L.jpg
[FILE] 31dgGEhZVZL.jpg
[FILE] 41+0fZlQNhL.jpg
[FILE] 317UEfHNWFL.jpg
[FILE] 31JogsMfUiL.jpg
[FILE] 31eCil-RbjL.jpg
[FILE] 31Qr3xgnfqS.jpg
[FILE] 31pSM+ji8sS.jpg
[FILE] 31pAbHSvESL.jpg
[FILE] 31fwpf6yMtL.jpg
[FILE] 31gjKIF3cgL.jpg
[FILE] 317K7+0KVPL.jpg
[FILE] 31AxondfXlL.jpg
[FILE] 31OAkCZ7OVL.jpg
[FILE] 312aMY3cO9L.jpg
[FILE] 31QY4R5UNwL.jpg
[FILE] 31r7Qyl1RnL.jpg
[FILE] 31NtW+XAQbS.jpg
[FILE] 31TMmrktpHS.jpg
[FILE] 314xpT+zaWL.jpg
[FILE] 31ALW6ILdNS.jpg
[FILE] 41+7YFt7FLS.jpg
[FILE] 31GcK11qXXL.jpg
[FILE] 31EIyTViitL.jpg
[FILE] 31fcc1LXQrL.jpg
[FI